# Ch 1: Overview
Welcome fellow traders! 

This is a Notebook on the My_Trading_Buddy. The aim of this project is to provide a assistance to a technical approach to trading on the ASX. The goal is for you to be equipt with the necessary tools to analyse market trends and simulate your personalised model! I have broken this up into chapters like a notebook. 

Best of Luck, 

Your trading buddy :)

## Ch 1.1: Import Packages

In [1]:
import yfinance as yf
import pandas as pd
from pandas_datareader import data as pdr
import matplotlib.pyplot as plt
import math
import numpy as np

import datetime as dt

import plotly.offline as pyo
import plotly

import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)

## Ch 1.2: Scrapping Data and Stock Overview 

In [64]:
# Define Start and End dates

end = dt.datetime.now()
end = dt.datetime(2019,7,7)
start  = dt.datetime(2016,12,12)

In [65]:
# Define Stocks of interest

stocklist = ['MQG','CBA', 'NAB', 'WBC','BOQ','QAN','VAS']
#stocklist = ['MQG','CBA']
#stocklist = ['QAN','ATEC','VAS','NDQ']
stocks = [i + '.AX' for i in stocklist]

In [66]:
# Use the Daily Opening data
import fix_yahoo_finance as yf
df = yf.Ticker(stocks, start,end)
df_price = df.Open
df = df.Open

# Display Stock Info
import plotly.offline as pyo
pyo.init_notebook_mode(connected = True)
pd.options.plotting.backend = 'plotly'
df_price.plot()

[*********************100%***********************]  7 of 7 completed


def std_data(data, n = 365, percentage = '50%'):
    data_yr = data[data.index > end - dt.timedelta(days = n)].copy()
    for i in stocks:
        median = data_yr.describe(percentiles=[0.1,0.5,0.9])[i][percentage]
        print(i,median)
        data_yr[i] = data_yr.loc[:,(i)].div(median)
    return data_yr
st = std_data(df)
st.plot()

df['MQG.AX'].pct_change().plot(kind='hist')

## Ch 1.2i: Quick testing algorithm


In [5]:
def final_results(df, stocks = stocks):
    final_array = []
    for stock in stocks:
        final_array.append(round(df[stock][-1],5))
    print('Stocks: ',stocks)
    print('Results:',final_array)
    print('Average: {}'.format(round(sum(final_array)/len(final_array),2)))

## Ch 1.3 Standard Models to Compare 
This section is prebuilt algorithms (from scratch) that are common trading strategies. It is important to compare your proposed model/algorithm against these standards as we want our model to be smarter than the more common trading strategies.

Be sure to use the appropriate Standard model for your assumptions

###  Ch 1.3a Buy and Hold
The Classic buy at the start of your trading period and sell on the last day

This is a very good strategy when you have a large sum of money at the start of your trading period

In [35]:
def buy_n_hold(p_df, start = dt.timedelta(days = 365), end = dt.datetime.now(), n = 0, stocks = ['CBA.AX'], mode = 'value',
            total_investment = None, brokerage_fee = 20):
    if n != 0:
        start = dt.timedelta(days = n)
    #price_df = p_df[p_df.index > end - start].copy()
    price_df = p_df
    df = pd.DataFrame(index = p_df.index)
    new_df = df
    #new_df = df[df.index > end - start].copy()
    
    for stock in stocks:
        initial = price_df[stock][0]
        final = price_df[stock][-1]
        step = (final - initial) / len(new_df)
        value_array = []
        percentage_array = []

        if total_investment != None:
            stock_num = (total_investment - brokerage_fee) / initial
            for day_index in range(len(price_df[stock])):
                current_value = (initial + step * day_index) 
                value_array.append(current_value * stock_num)
                percentage_array.append(((current_value / initial) - 1) * 100)
        elif total_investment == None:
            for day_index in range(len(price_df[stock])):
                current_value = initial + step * day_index
                value_array.append(current_value)
                percentage_array.append(((current_value / initial) - 1) * 100)

        if mode == 'value':
            new_df[stock] = value_array
        elif mode == 'percentage':
            new_df[stock] = percentage_array
    return new_df
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 7000, stocks = stocks, n = 3000)
final_results(bnh)
bnh.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
Results: [429.92254, 66.66088, 16.43274, 33.01512, 24.49995, 225.47975, 53.73475]
Average: 121.39


### Ch 1.3b Dollar Cost Average
A strict stategy where you input the same fixed value for a specific period. The idea is that you purchase more stocks when the market is down, and purchase less stocks when the market is up.

This strategy is good for investors who have a steady stream of income they want to invest in and if the market is continuously going up

In [7]:
def doll_cost_av(p_df, day_freq = 60, trade_amount = 5000, stocks = ['CBA.AX'], brokerage_fee = 20, 
                 mode = 'value', start = dt.timedelta(days = 365), end = dt.datetime.now(), n = 0):
    if n != 0:
        start = dt.timedelta(days = n)
    df = pd.DataFrame(index = p_df.index)
    #new_df = df[df.index > end - start].copy()
    new_df = df
    #price_df = p_df[p_df.index > end - start].copy()
    price_df = p_df
    inv_amount = 0
    inv_array = []
    inv_counter = 0
    for time_index in price_df[stocks].index:
        # trade on the first day
        if len(inv_array) == 0:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter != day_freq: 
            inv_array.append(inv_amount)
            inv_counter += 1
        elif inv_counter == day_freq:
            inv_amount += trade_amount
            inv_array.append(inv_amount)
            inv_counter = 0
    #print(inv_array)
    new_df['invested'] = inv_array

    # dollar cost average
    for stock in stocks:
        price_amount = 0
        price_array = []
        day_counter = 0
        stock_amount = 0
        value_delta_array = []
        for time_index in price_df[stocks].index:
            if len(price_array) == 0:
                price_amount += trade_amount
                #print(stock,time_index,price_df[stock][time_index])
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(price_amount)
                value_delta_array.append(0)
                day_counter += 1
            elif day_counter != day_freq: 
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter += 1
            elif day_counter == day_freq:
                price_amount += trade_amount
                stock_amount += (trade_amount- brokerage_fee) / price_df[stock][time_index]
                price_array.append(stock_amount * price_df[stock][time_index])
                value_delta_array.append(stock_amount * price_df[stock][time_index] - new_df['invested'][time_index])
                day_counter = 0
            #print(price_amount)
            
        if mode == 'percentage':
            new_df[stock] = ((price_array / new_df['invested']) -1 )* 100 
        elif mode == 'value':
            new_df[stock] = price_array
        elif mode == 'value_delta':
            new_df[stock] = value_delta_array
    if mode == 'percentage' or mode == 'value_delta':
        new_df.drop(columns=['invested'], inplace=True)
    
    return new_df

dca = doll_cost_av(p_df = df_price, mode = 'value_delta', stocks = stocks)
final_results(dca)
#print(dca)
dca.plot()

Stocks:  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
Results: [14138.29613, 4730.23767, -2107.88642, -2537.15422, -7542.9316, 4271.19899, 6830.57188]
Average: 2540.33


## Ch 1.4: Compare Algorythms

In [117]:
def compare_results_beta(df_1, df_2, stocks = ['CBA.AX']):
    results_array = []
    for stock in stocks:
        df1_result = df_1[stock][-1]
        df2_result = df_2[stock][-1]
        difference = (df1_result - df2_result)
        results_array.append(difference)
        print('Stock: {}, {}%'.format(stock, round(difference,2)))
    print('Average result: {}%'.format(round(sum(results_array)/len(results_array),2)))
    



n = 365
mode = 'percentage'

bnh = buy_n_hold(p_df = df_price, mode = mode, n = n, stocks = stocks, total_investment = 8000)
dca = doll_cost_av(p_df = df_price, mode = mode, n = n, stocks = stocks)
compare_results_beta(df_1 = bnh, df_2 = dca, stocks = stocks)

Stock: MQG.AX, 25.59%
Stock: CBA.AX, -6.93%
Stock: NAB.AX, -5.72%
Stock: WBC.AX, -7.91%
Stock: BOQ.AX, -3.92%
Stock: QAN.AX, 55.4%
Stock: VAS.AX, 7.5%
Average result: 9.15%


In [124]:
def compare_results(df_1, df_2, stocks = ['CBA.AX'], mode = 'percentage'):
    df_1_results = []
    df_2_results = []
    for stock in stocks:
        df_1_results.append(round(df_1[stock][-1],6))
        df_2_results.append(round(df_2[stock][-1],6))
    print('Stocks name:', stocks)
    print('Algorithm 1:', df_1_results)
    print('Algorithm 2:', df_2_results)
    stats_comparison = []
    for i in range(len(df_1_results)):
        stats_comparison.append(round(df_1_results[i] - df_2_results[i],6))
    print('Difference :', stats_comparison)
    if mode == 'percentage':
        print('Average    : {}%'.format(round(sum(stats_comparison)/len(stats_comparison),2)))  
    elif mode == 'value':
        print('Average    : ${}'.format(round(sum(stats_comparison)/len(stats_comparison),2)))
compare_results(df_1 = price_1, df_2 = price_2, stocks = stocks, mode = 'percentage') 

Stocks name: ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
Algorithm 1: [23.386658, 1.098365, 6.121541, -11.690199, -7.409706, 32.340312, 2.01681]
Algorithm 2: [22.146008, -4.698652, -4.044244, -5.388712, 2.954615, 15.503142, 1.632536]
Difference : [1.24065, 5.797017, 10.165785, -6.301487, -10.364321, 16.83717, 0.384274]
Average    : 2.54%


Need to finish this
def compare_graphs(df1, df2):
    

# Ch 2: Building a New Algorithm

## Ch 2.1: First Algorithm
We standardise each stock performance by dividing it by the rolling median/mean (so we can compare each stock). 

Realising the area under this transformed graph is a better indicator for stock market value. This shows the overall growth of the stock.

Since stock values a year ago is less important information for us than stock values last week, we must include a reduction factor.

We will then put a make a threshold for the new graph and determine when to trade.

In [67]:
# Inputs: df with stock prices
# Outputs a rolling normalised df for all stocks

# Normalises using a rolling median
def norm_df_med(df, window = 30, stocks = ['CBA.AX']):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = (df[stock] / df[stock].rolling(window, min_periods = 0).median() -1)
    return new_df

# Normalises using rolling mean
def norm_df_mean(df, window = 30,  stocks = ['CBA.AX']):
    new_df = pd.DataFrame()
    for stock in stocks:
        new_df[stock] = df[stock] / df[stock].rolling(window, min_periods = 0).mean()-1
    return new_df

gradient = norm_df_med(df,window = 20, stocks = stocks)

In [68]:
# Inputs: normalised stock prices df
# Outputs: area under the graph with a reduction factor df

def norm_sum_df(gradient, reduction_factor  = 1 , stocks = ['CBA.AX']):
    new_df = pd.DataFrame(index = gradient.index)
    for stock in stocks:
        totals = []
        rolling_sum = 0
        for time_index in df.index:
            rolling_sum = (rolling_sum * reduction_factor + gradient[stock][time_index])
            totals.append(rolling_sum)
        new_df[stock] = totals
    return new_df
integral = norm_sum_df(gradient = gradient, reduction_factor = 0.9, stocks = stocks)
#integral.plot()
#print(df_2)

In [147]:
# Input: 2 dfs, the first being the transformed df and another being the df with pricing
#        can also input upper and lower threshholds

# Output: df that determines to trade or not based on threshholds
#         also outputs stock price for each given day

def trade_list(integral = integral, df_price = df_price, stocks = ['CBA.AX'], 
               up_thresh = 0.9, low_thresh = 0.25, thresh_window = 180, trig_thresh = 20):
    decisions = pd.DataFrame(index = integral.index)
    for stock in stocks:
        #trim_df = df[df.index > end - start]
        trim_df = integral
        n_df = integral
        #trim_df_price = df_price[df_price.index > end - start]
        trim_df_price = df_price
        #n_df = (trim_df)

        new_df = pd.DataFrame(index = integral.index)
        new_df['price'] = df_price[stock]
        new_df['norm'] = integral[stock]
        new_df['up_bound'] = integral[stock].rolling(thresh_window, min_periods = 0).quantile(up_thresh).copy()
        new_df['low_bound'] = integral[stock].rolling(thresh_window, min_periods = 0).quantile(low_thresh).copy()

        trade = []
        buy_trig, sell_trig = 0, 0   
        cooler_counter = 0
        for time_index in integral[stock].index:
            if integral[stock][time_index] > new_df['up_bound'][time_index] and sell_trig == 0 and cooler_counter > 10:
                sell_trig = 1
                trade.append(1)
            elif integral[stock][time_index] < new_df['low_bound'][time_index] and buy_trig == 0 and cooler_counter > 10:
                buy_trig = 1
                trade.append(-1)
            else:
                trade.append(0)
            cooler_counter+=1

            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                buy_trig = 0 

        new_df['trade'] = trade
        decisions[stock] = trade
    return decisions
decide = trade_list(integral = integral, df_price = df_price, stocks = stocks,up_thresh = 0.6, low_thresh = 0.4, thresh_window = 180,
                    trig_thresh = 20)
#decide.plot()

### Ch 2.1a: Run Algorithm 1

In [148]:
stocks_var = stocks
# Gradient
window = 20

# Integral
integral_reduction_factor = 0.9

# Decide
low_thresh = 0.1
up_thresh = 0.6
thresh_window = 180
trade_delay = 20

# Trading
brokerage_fee = 20
compound_factor = None
amount_per_trade = 6000
bank = 8000
mode = 'percentage'

gradient = norm_df_med(df, window = window, stocks = stocks_var)
integral = norm_sum_df(gradient = gradient, reduction_factor = integral_reduction_factor, stocks = stocks_var)
decide_1 = trade_list(integral = integral, df_price = df_price, stocks = stocks_var,
                      low_thresh = low_thresh, up_thresh = up_thresh , thresh_window = thresh_window, 
                      trig_thresh = trade_delay)
price_1 = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks_var, mode = mode,
                         brokerage_fee = brokerage_fee, trade_amount = amount_per_trade, 
                         compound_factor = compound_factor, bank = bank)
#compare_results(df_1 = price_1, df_2 = price_2, stocks = stocks, mode = mode)

Trade Output: percentage


### Ch 2.1b: Running Some Stats

In [149]:
def risk_stats(decide = decide_1, df_price = df_price, stocks = stocks, mode = 'value', 
              brokerage_fee = 20, trade_amount = 6000, compound_factor = None, bank = 8000):
    wallet_df = pd.DataFrame(index = df_price.index)
    value_price = trade_price_df(price_df = df_price, decision_trade_df = decide, stocks = stocks, mode = mode,
                   brokerage_fee = brokerage_fee, trade_amount = trade_amount, 
                   compound_factor = compound_factor, bank = bank)
    total_array = []
    for time_index in wallet_df.index:
        total_array.append(sum(sum(value_price[value_price.index == time_index].values)))
    wallet_df['running_total'] = total_array
    wallet_df['running_total'].plot()
    fin = wallet_df['running_total'][-1]/(bnk*len(stocks))
    most = wallet_df['running_total'].max()/(bnk*len(stocks))
    least = wallet_df['running_total'].min()/(bnk*len(stocks))
    print('Statistics for over-all')
    print('Finishing percentage: {}%'.format(round((fin-1)*100,2)))
    print('Highest Percentage:   {}%'.format(round((most-1)*100,2)))
    print('Lowest Percentage:   {}%'.format(round((least-1)*100,2)))
#risk_stats()
risk_stats(decide = decide_1, df_price = df_price, compound_factor = 1)

Trade Output: value
Statistics for over-all
Finishing percentage: 4.86%
Highest Percentage:   4.86%
Lowest Percentage:   -75.0%
Trade Output: value
Statistics for over-all
Finishing percentage: 6.73%
Highest Percentage:   6.9%
Lowest Percentage:   -100.0%


## Ch 2.2: Second Algorithm
We will use the standardised rolling median as well as the integral function to work out the best trading pattern.

Using the rolling median graph as the gradient, we can determine when the graph intercepts with the horizontal axis and thus finding the dip of the area graph. Once that has occured we need to set a threshold for the area graph beyond which will trade to remove any uneccesary trades

## Standard Trading Strategies

 I am unsure whether my designed trading strategy is effective (sometimes the trading season is strong, leading to strong trading simulations. Sometimes the trading season is weak, leading to bad trading seasons), so I devise two models to compare our trading algorithm against:
 1. Buy_n_sell: Buy a fixed amount at the start of a period and hold onto it with no buying or selling in between.
 2. Dollar Cost Average: Purchase shares in fixed time interval with a fixed cap of money

It is good to note, both these algorythms are strong in a uniformly increasing market which is not the case in the current market (Jan 2023)

###################### This is a working copy
def trading_results(df, amount_per_trade = 8000, bank = 20000, brokerage_fee = 20):
    holding_stocks = 0
    total_value = []
    for i in df.index:
        if (df['trade'][i] == -1) & (bank >= amount_per_trade):
            # print('buy')
            bank += -amount_per_trade
            holding_stocks += (amount_per_trade - brokerage_fee) / df['price'][i]
        elif (df['trade'][i] == 1) and (holding_stocks > 0):
            # print('sell')
            bank += holding_stocks * df['price'][i] - brokerage_fee
            holding_stocks = 0
        total_value.append(bank)
    
    total_value[-1] = bank + holding_stocks * int(df['price'][-1])
    df['value'] = total_value
    return df

#norm_df_med(df, window = 30).plot()
df_1yr = df[df.index > end - dt.timedelta(days = 3000)]
df_1yr_norm = norm_df_med(df_1yr,window = 30)

cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k=0
fig_norm_comp = make_subplots(rows = 3, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('Bank Stocks','Normalised Stocks'),
                   row_width = [0.5,0.5,0.5])
test = norm_df_sum(df_1yr_norm)
for i in df_1yr:
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr.index, y = df_1yr[i], name = i, 
                                       legendgroup = i, marker=dict(color=cols[k])), row =1, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = test[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =2, col = 1)
    fig_norm_comp.add_trace(go.Scatter(x=df_1yr_norm.index, y = df_1yr_norm[i], name = i, 
                                       showlegend = False, legendgroup = i, marker=dict(color=cols[k])), row =3, col = 1)
    k += 1
fig_norm_comp

In [100]:
def norm_int_df(norm_df, stocks = ['CBA.AX']):
    new_df = pd.DataFrame(index = norm_df.index)
    for stock in stocks:
        crossing_array = []
        for time_index in range(len(norm_df[stock])):
            if time_index == 0:
                crossing_array.append(0)
            elif norm_df[stock][time_index - 1] < 0 and norm_df[stock][time_index] >= 0:
                # indicate to buy
                crossing_array.append(-1)
            elif norm_df[stock][time_index - 1] >= 0 and norm_df[stock][time_index] < 0:
                # indicate to sell
                crossing_array.append(1)
            else: 
                crossing_array.append(0)
        new_df[stock] = crossing_array
    return new_df
df_3 = norm_int_df(df_1, stocks = stocks)
df_3.plot()          



def decision_trade_df(norm_int_df = df, norm_sum_df = df, threshold = 0.5, stocks = ['CBA.AX'],
                     trig_thresh = 20):
    new_df = pd.DataFrame(index = norm_int_df.index)
    for stock in stocks:
        trade_array = []
        upper_limit, lower_limit = 0,0
        buy_trig, sell_trig, cooler_counter = 0, 0, 0
        for time_index in range(len(norm_int_df)):
            if norm_int_df[stock][time_index] == 1 and norm_sum_df[stock][time_index] > threshold * upper_limit and sell_trig == 0 and cooler_counter > 5:
                upper_limit = norm_sum_df[stock][time_index]
                trade_array.append(1)
                sell_trig = 1
            elif norm_int_df[stock][time_index] == -1 and norm_sum_df[stock][time_index] < threshold * lower_limit and buy_trig == 0 and cooler_counter > 5:
                lower_limit = norm_sum_df[stock][time_index]
                trade_array.append(-1)
                buy_trig = 1
            else:
                trade_array.append(0)
            
            cooler_counter += 1
               
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                
                buy_trig = 0 
        new_df[stock] = trade_array
    return(new_df)
#print(df_2)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2, stocks = stocks)
df_4.plot()

In [102]:
# Input: intercept indicator df and normalised area df
# Output: trade df 
# Gradient = 0, check area graph if its large enough, then buy/sell

def decision_trade_df(norm_int_df = df, norm_sum_df = df, limit_factor = 1, stocks = ['CBA.AX'],
                     trig_thresh = 20):
    new_df = pd.DataFrame(index = norm_int_df.index)
    for stock in stocks:
        trade_array = []
        pos_limit, neg_limit = [],[]
        upper_limit, lower_limit = 0,0
        buy_trig, sell_trig, cooler_counter = 0, 0, 0
        for time_index in range(len(norm_int_df)):
            if norm_sum_df[stock][time_index] >= 0:
                pos_limit.append(norm_sum_df[stock][time_index])
                upper_limit = sum(pos_limit)/len(pos_limit)
            elif norm_sum_df[stock][time_index] < 0:
                neg_limit.append(norm_sum_df[stock][time_index])
                lower_limit = sum(neg_limit)/len(neg_limit)
                
            #print(upper_limit,lower_limit)
            if norm_int_df[stock][time_index] == 1 and norm_sum_df[stock][time_index] > limit_factor * upper_limit and sell_trig == 0 and cooler_counter > 5:
                upper_limit = norm_sum_df[stock][time_index]
                trade_array.append(1)
                sell_trig = 1
            elif norm_int_df[stock][time_index] == -1 and norm_sum_df[stock][time_index] < limit_factor * lower_limit and buy_trig == 0 and cooler_counter > 5:
                lower_limit = norm_sum_df[stock][time_index]
                trade_array.append(-1)
                buy_trig = 1
            else:
                trade_array.append(0)
            
            cooler_counter += 1
               
            #Triggers for sell
            if sell_trig < trig_thresh and sell_trig > 0:
                sell_trig += 1
            elif sell_trig == trig_thresh:
                sell_trig = 0

            #Triggers for buy
            if buy_trig < trig_thresh and buy_trig > 0:
                buy_trig += 1
            elif buy_trig == trig_thresh:
                
                buy_trig = 0 
        new_df[stock] = trade_array
    return(new_df)
#print(df_2)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2, stocks = stocks)
df_4.plot()

In [133]:
def trade_price_df(price_df = df_price, decision_trade_df = df, brokerage_fee = 20, 
                   trade_amount = 6000, compound_factor = None, bank = 8000, mode = 'percentage',
                  stocks = ['CBA.AX']):
    bank_initial = bank
    print('Trade Output:', mode)
    #print(decision_trade_df)
    new_df = pd.DataFrame(index = decision_trade_df.index)

    #if trade_amount > 10000:
    #    brokerage_fee = 30
    for stock in stocks:
        bank = bank_initial
        if compound_factor != None:
            trade_amount = compound_factor * bank
        holding_stocks = 0
        bank_value = []
        total_value = []
        for date_index in decision_trade_df[stock].index:
            if (decision_trade_df[stock][date_index] == -1) & (bank >= trade_amount): 
                # print('buy')
                bank += - trade_amount
                holding_stocks += (trade_amount - brokerage_fee) / price_df[stock][date_index]
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            elif (decision_trade_df[stock][date_index] == 1) and (holding_stocks > 0):
                # print('sell')
                bank += holding_stocks * price_df[stock][date_index] - brokerage_fee
                holding_stocks = 0
                if compound_factor != None:
                    trade_amount = compound_factor * bank
            bank_value.append(bank)
            
            if math.isnan(price_df[stock][date_index]) == True:
                total_value.append(bank)
            else:
                total_value.append(bank + holding_stocks * int(price_df[stock][date_index]))
        last_index = -1
        while math.isnan(price_df[stock][last_index]) == True:
            last_index += -1
        else:
            bank_value[-1] = bank + holding_stocks * int(price_df[stock][last_index])
            #print(stock,bank_value[-21],bank_value[-1])
        
        if mode == 'value':
            new_df[stock] = bank_value
        elif mode == 'bank':
            new_df[stock] = total_value
        elif mode == 'percentage':
            new_df[stock] = ((np.array(total_value) / bank_initial) -1) * 100
    return(new_df)
stocks = [i + '.AX' for i in stocklist]

df_5 = trade_price_df(price_df = df_price, decision_trade_df = df_4, stocks = stocks, mode = 'value')
df_5.plot()

Trade Output: value


In [112]:
#This is a test
stocks = [i + '.AX' for i in stocklist]
sample = norm_df_med(df, window = 60, stocks = stocks)
df_2 = norm_sum_df(df_1, reduction_factor = 0.95, stocks = stocks)
df_3 = norm_int_df(df_1, stocks = stocks)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2,stocks = stocks, limit_factor = 1, trig_thresh = 20)
df_5 = trade_price_df(price_df = df_price, decision_trade_df = df_4,stocks = stocks, mode = 'value', compound_factor = 1, brokerage_fee = 20)
#df_1.plot()

df_5_finish = []
for i in stocks:    
    df_5_finish.append(round(df_5[i][-1],6))
print(stocks)
print(df_5_finish)
print(round(sum(df_5_finish)/len(df_5_finish)/80,2), '%')
df_5.plot()

Trade Output: value
['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
[9026.786699, 7499.892897, 7491.006731, 7251.462475, 6911.520783, 7468.717108, 9234.563845]
98.01 %


In [75]:
#This works well
stocks = [i + '.AX' for i in stocklist]
df_1 = norm_df_med(df, window = 60, stocks = stocks)
df_2 = norm_sum_df(df_1, reduction_factor = 0.95, stocks = stocks)
df_3 = norm_int_df(df_1, stocks = stocks)
df_4 = decision_trade_df(norm_int_df = df_3, norm_sum_df = df_2,stocks = stocks, limit_factor = 1, trig_thresh = 20)
df_5 = trade_price_df(price_df = df_price, decision_trade_df = df_4,stocks = stocks, mode = 'value', compound_factor = 1, brokerage_fee = 20)
#df_1.plot()

df_5_finish = []
for i in stocks:    
    df_5_finish.append(round(df_5[i][-1],6))
print(stocks)
print(df_5_finish)
print(round(sum(df_5_finish)/len(df_5_finish)/80,2), '%')
df_5.plot()

NameError: name 'norm_int_df' is not defined

df_2.plot()

df_3.plot()

df_4.plot()

In [128]:
stocks = ['BOQ.AX']#, 'MQG.AX']
#df_1 = norm_df_med(df, window =20)
#df_2 = norm_df_sum(df_1, reduction_factor = 0.9, n = 365)
testing_graph = make_subplots(rows = 1, cols = 1,
                    subplot_titles = ('Testing Group'))
cols = plotly.colors.DEFAULT_PLOTLY_COLORS
k = 0
for i in stocks:
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_1[i] * 8, name = i+' gradient', 
                                       showlegend = True, legendgroup = i+' gradient', marker=dict(color=cols[k])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_2[i]*1.5, name = i + ' Area', 
                                       showlegend = True, legendgroup = i + ' Area', marker=dict(color=cols[k+1])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_price[i]*0.08, name = i+' price', 
                                       showlegend = True, legendgroup = i+' price', marker=dict(color=cols[k+2])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_3[i], name = i+' int', 
                                      showlegend = True, legendgroup = i+' int', marker=dict(color=cols[k+3])))
    testing_graph.add_trace(go.Scatter(x = df_1.index, y = df_4[i], name = i+' trade', 
                                      showlegend = True, legendgroup = i+' trade', marker=dict(color=cols[k+4])))
    k+=1
testing_graph.show()

df_5.plot()

In [466]:
bnh = buy_n_hold(p_df = df_price, mode = 'percentage', total_investment = 8000, stock_list = stocks)
bnh_finish = []
df_5_finish = []
for i in stocks:
    #print('Stock {}: {}%'.format(i, round(bnh[i][-1],2)))
    bnh_finish.append(round(bnh[i][-1],6))
    df_5_finish.append(round(df_5[i][-1],6))

print('Stocks name ', stocks)
print('My Algorythm', df_5_finish)
print('BnH standard', bnh_finish)
stats_comparison = []
for i in range(len(bnh_finish)):
    stats_comparison.append(round(df_5_finish[i] - bnh_finish[i],6))
print('Difference  ',stats_comparison)
print('Average:    ', round(sum(stats_comparison)/len(stats_comparison),2),'%')

Stocks name  ['MQG.AX', 'CBA.AX', 'NAB.AX', 'WBC.AX', 'BOQ.AX', 'QAN.AX', 'VAS.AX']
My Algorythm [25.578987, -16.71909, -5.714175, -5.833374, -17.155973, -16.059714, -0.588968]
BnH standard [51.295558, 1.670892, -9.548949, -12.519288, -17.634996, 63.167366, 19.918434]
Difference   [-25.716571, -18.389982, 3.834774, 6.685914, 0.479023, -79.22708, -20.507402]
Average:     -18.98 %


In [113]:
#norm_sum_df(norm_df_med(df, window = 60, stocks = stocks),stocks = stocks, reduction_factor = 0.9)['WBC.AX'].plot()
gradient = norm_df_med(df,stocks = stocks, window = 20)
#gradient['WBC.AX'].plot()
integral = norm_sum_df(gradient, stocks = stocks, reduction_factor = 0.9)
#integral['WBC.AX'].plot()
intercepts = norm_int_df(gradient, stocks = stocks)
#intercepts['WBC.AX'].plot()
decide_2 = decision_trade_df(norm_int_df = intercepts, norm_sum_df = integral, stocks = stocks, limit_factor = .8)
#decide['WBC.AX'].plot()
price_2 = trade_price_df(price_df = df_price, decision_trade_df = decide_2, stocks = stocks, mode = 'percentage')
#print(price_2)
price_2['WBC.AX'].plot()

Trade Output: percentage


In [243]:
compare_results(pricing, bnh, stocks = stocks)

Stock: MQG.AX, -27.8%
Stock: CBA.AX, -11.94%
Stock: NAB.AX, 2.96%
Stock: WBC.AX, -3.77%
Stock: BOQ.AX, 19.63%
Stock: QAN.AX, -65.31%
Stock: VAS.AX, -10.24%
Average result: -13.78%


# Another Tutorial

a = trade_list(df, stock = 'NAB.AX', start = dt.timedelta(days = 365))
trading_results(a)['value'].plot()

In [409]:
fig_test = make_subplots(rows = 1, cols = 1)
finish = []
sd_df = norm_df_mean(df, window = 30)
for i in stocks:
    a = trade_list(sd_df,df_price = df_price, stock = i, start = dt.timedelta(days = 365), 
                  )
    results = trading_results(a)
    finish.append(((results['value'][-1]/20000)-1)*100)
    fig_test.add_trace(go.Scatter(x=a.index, y = ((results['value']/20000)-1)*100,  name = i), row =1, col = 1)
#fig_test.show()
print(finish)
print(sum(finish)/len(finish))
print(a)
#a['low_bound'].plot()

[-25.56272558207242, -1.3481754923096334, 3.4862993740140125, -22.46191120011597, -19.320223079112985, -30.14035032061031, -17.70906449313545]
-16.150878684763253
            price      norm  up_bound  low_bound  trade         value
Date                                                                 
2021-12-24   8.13  1.019862  1.036889   0.980009      0  20000.000000
2021-12-29   8.23  1.033530  1.036889   0.980009      0  20000.000000
2021-12-30   8.20  1.030885  1.036889   0.980009      0  20000.000000
2021-12-31   8.09  1.018250  1.034887   0.980009      0  20000.000000
2022-01-04   8.32  1.046760  1.034887   0.980009      1  20000.000000
...           ...       ...       ...        ...    ...           ...
2022-12-15   6.92  0.960489  1.064937   0.957574      0  16458.187101
2022-12-16   6.80  0.945977  1.064937   0.956672      0  16458.187101
2022-12-19   6.82  0.950523  1.064937   0.955172      0  16458.187101
2022-12-20   6.77  0.945883  1.064937   0.954861      0  16458.1871

In [413]:
#a['up_bound'].plot()

In [410]:
fig_test.update_layout(
    title = 'Trading Data',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Percentage Gain',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)

## Graphing Multiple graphs

In [187]:
print(new_df)

              CBA.AX    NAB.AX    WBC.AX    ANZ.AX    MQG.AX    BOQ.AX  \
Date                                                                     
2015-01-01  1.000000  1.000000  1.000000  1.000000  1.000000  1.000000   
2015-01-04  1.001223  1.000744  0.998344  0.999068  0.998974  0.998769   
2015-01-05  0.994868  0.993445  0.991255  0.987877  0.977063  0.977814   
2015-01-06  0.995206  0.997910  0.990156  0.992025  0.991367  0.990460   
2015-01-07  1.000000  1.004768  0.998175  1.000000  1.000000  1.000000   
...              ...       ...       ...       ...       ...       ...   
2022-12-11  0.995231  0.965153  0.981513  0.956716  0.965436  0.947586   
2022-12-12  1.005147  0.984965  0.995582  0.981270  0.973092  0.966184   
2022-12-13  1.007444  0.982877  0.992003  0.979001  0.980691  0.967519   
2022-12-14  1.003382  0.989078  0.989265  0.977505  0.966505  0.957123   
2022-12-15  1.003194  0.992745  0.990099  0.979910  0.966505  0.957785   

             A200.AX  
Date          

In [17]:
import datetime as dt
import pandas as pd
from pandas_datareader import data as pdr
import plotly.offline as pyo
import plotly.graph_objects as go
from plotly.subplots import make_subplots

pyo.init_notebook_mode(connected=True)

In [107]:
end = dt.datetime.now()
start = dt.datetime(2015,1,1)

df = yf.Ticker('CBA.AX', start,end)
df.head

[*********************100%***********************]  1 of 1 completed


<bound method NDFrame.head of                   Open        High         Low       Close   Adj Close  \
Date                                                                     
2015-01-02   84.959686   85.277962   84.661308   85.277962   58.036251   
2015-01-05   85.238182   85.775269   85.049202   85.486832   58.178394   
2015-01-06   84.641411   85.337639   84.412651   84.840332   57.738411   
2015-01-07   84.850281   85.029312   84.094376   84.651360   57.609806   
2015-01-08   85.079041   85.188446   84.671249   84.929848   57.799339   
...                ...         ...         ...         ...         ...   
2022-12-14  106.620003  107.059998  105.839996  106.919998  106.919998   
2022-12-15  106.699997  107.690002  106.220001  106.800003  106.800003   
2022-12-16  106.059998  106.290001  105.160004  105.980003  105.980003   
2022-12-19  105.000000  105.760002  104.750000  105.629997  105.629997   
2022-12-20  105.809998  106.110001  104.930000  105.330002  105.330002   

       

In [108]:
df['MA50'] = df['Close'].rolling(window = 50, min_periods = 0).mean()
df['MA200'] = df['Close'].rolling(window = 200, min_periods = 0).mean()

df['ME30'] = df['Close'].rolling(window = 30, min_periods = 0).median()


In [109]:
fig = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [110]:
fig.add_trace(go.Candlestick(x = df.index, open= df['Open'], high = df['High'], low = df['Low'], close = df['Close'], 
                             name = 'OHLC'
                            ),row = 1, col = 1)
1

1

In [111]:
fig.add_trace(go.Scatter(x=df.index, y = df['MA50'], marker_color = 'grey', name = 'MA50'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['MA200'], marker_color = 'lightgrey', name = 'MA200'), row =1, col = 1)
fig.add_trace(go.Scatter(x=df.index, y = df['ME30'], marker_color = 'blue', name = 'ME30'), row =1, col = 1)
1

1

In [112]:
fig.add_trace(go.Bar(x = df.index, y = df['Volume'], marker_color = 'red', showlegend = False), row = 2, col = 1)
1

1

In [113]:
fig.update_layout(
    title = 'CBA historical price chart',
    xaxis_tickfont_size = 12,
    yaxis = dict(
        title = 'Price ($/share)',
        title_font_size = 14,
        tickfont_size = 12),
    autosize = False,
    width = 800,
    height = 500,
    margin = dict(l = 50, r = 50, b = 100, t = 100, pad =5),
    paper_bgcolor = 'aliceblue'
)
1

1

In [114]:
fig.update(layout_xaxis_rangeslider_visible = False)

In [31]:
fig_test = make_subplots(rows = 2, cols = 1, shared_xaxes = True,
                   vertical_spacing = 0.1, subplot_titles = ('CBA','Volume'),
                   row_width = [0.2,0.7])

In [216]:
a=[3,90,3,7,8,100]
if [sum(a)<100]:
    a.append(2)
print(a)

[3, 90, 3, 7, 8, 100, 2]


In [217]:
a=[3,90,3,7,8,100]
if sum(a)<100:
    a.append(2)
print(a)

[3, 90, 3, 7, 8, 100]
